In [4]:
print("helloooo")

helloooo


In [24]:
from river.tree import HoeffdingTreeClassifier
from river import stream
from river import metrics
from river import evaluate

import time
import datetime as dt
import pandas as pd
import os
import random

import argparse

PATH_TO_DATA = "C:/Users/Bayde/Desktop/Hoeffding_Tree_Project_Data/datasets_csv"
       
    
"""
Grace period: The number of instances a leaf should observe between split attempts. Range
of values (10; 200). Step = 10.

Split Confidence: The allowable error in split decision. Range of values (0.0; 1.0). Step =
0.05.

Tie Threshold: Threshold below which a split will be forced to break ties. Range of values
(0.0; 1.0). Step = 0.05.
"""
        
        
def model_size(model):
    if str(model) == 'HoeffdingTreeClassifier':
        return model.n_nodes
    elif str(model) == 'ARFClassifier':     # In case we are interested in counting the number of nodes from all trees.
        nodes = 0
        for m in model.models:
            nodes += m.model.n_nodes
        return nodes
    return -1


def run_experiment(ensemble, dataset, window_size):
    accuracy = metrics.Accuracy()
    start = time.perf_counter()

    X, Y = dataset[:, :-1], dataset[:, -1]
    # Downsampling the data
    # Select every 20th element starting from the first element
    # Useful during development, when you are making sure your
    #    algorithm works before doing the actual experiments.
    
    X, Y = X[::20], Y[::20]  #TODO: <--- Remember to remove downsampling

    accuracies = []
    predictions = []
    for x in range(len(ensemble)):
        accuracies.append(metrics.Accuracy())
        predictions.append([])
        
    en_acc = metrics.Accuracy()
    en_predict = []
    
    candidate = new_tree()
    cand_acc = metrics.Accuracy()
    cand_pre = []
        
    ds = stream.iter_array(X, Y)
    counter = 0
    for (x, y) in ds:
        
        #trees:
        for i in range(len(ensemble)):
            yp = ensemble[i].predict_one(x)
            predictions[i].append(yp)
            ensemble[i].learn_one(x, y)
            accuracies[i].update(y,yp)
         
        #candidate tree:
        cyp = candidate.predict_one(x)
        cand_pre.append(cyp)
        candidate.learn_one(x, y)
        cand_acc.update(y,cyp)
        
        #ensemble:
        en_predict.append(vote(predictions, counter, accuracies))
        en_acc.update(y, en_predict[counter])
        
        
        if counter % window_size == 0: # Candidate tree time
            # if tree better than weakest swap in
            if cand_acc.get() < min(acc.get() for acc in accuracies):
                print("IGNORED")
            else:
                lowest_index = 99
                lowest_val = 1
                for x in range(len(ensemble)):
                    if accuracies[x].get() < lowest_val:
                        lowest_index = x
                        lowest_val = accuracies[x].get()
                ensemble[lowest_index] = candidate
                print("SWAPPED (", cand_acc.get(), " > ", lowest_val, ")")
                
            candidate = new_tree() # instantiate new candidate 
                
            
        
        counter = counter +1
        #accuracy.update(y, yp)
        print("Ensemble: {:.2f} Candidate: {:.2f} Trees: {}".format(en_acc.get(), cand_acc.get(), accuracies))
     
    return predictions
    #return accuracy.get(), dt.timedelta(seconds=time.perf_counter() - start).seconds, model_size(model)

    
def vote(pred, count, acc):
    w = {} # votes
    for model_num in range(len(pred)):
        # Get the prediction for the current model and instance
        prediction = pred[model_num][count] 
        accuracy = acc[model_num].get()

        if prediction not in w:
            w[prediction] = 0
        w[prediction] += accuracy

    # Grab max weighted value class
    ensemble_prediction = max(w, key=w.get)
    return ensemble_prediction
        
        
def new_tree():
    # Random grace period from the range (10, 200) with step = 10
    gp = random.choice(range(10, 201, 10))

    # Random split_confidence from the range (0.0, 1.0) with step = 0.05
    sc = random.choice([i * 0.05 for i in range(1, 21)])

    # Random tau from the range (0.0, 1.0) with step = 0.05
    t = random.choice([i * 0.05 for i in range(21)])

    new_model = HoeffdingTreeClassifier(
        grace_period=gp,
        delta=sc,
        tau=t)
    return new_model
    
    
    
    
    
def main(num_learners, window_size):
    
    # Optional HyperParameter Arguments for base HT Classifier, default is (10,0,0)
    print(f"Number of learners: {num_learners}")
    print(f"Candidate window size: {window_size}")
    
    datasets = ['electricity.csv', 'SEA_abrupt.csv', 'SEA_gradual.csv',
                'RTG_2abrupt.csv', 'covtype.csv']

    ensemble = []
    
    for x in range(num_learners):
        tree = new_tree()
        ensemble.append(tree)         

    for name in datasets: # For Each Dataset
        dataset = pd.read_csv(os.path.join(PATH_TO_DATA, name)).to_numpy()
        results = run_experiment(ensemble, dataset, window_size)
    print("---DONE---")
        

#         for model in models: # For Each Model
#             result = run_experiment(model, dataset)
#             print('Dataset: ', name, ' Learner: ', model, ' Result: ', result, "(Accuracy, Time,  Size)")

            
            
if __name__ == '__main__':
#     parser = argparse.ArgumentParser(
#         description='hyperparameters for ensemble, default number of learners is 10, default candidate window is 1000.')

#     parser.add_argument('--S', type=int, choices=range(1, 50, 1),
#                         help='The number of trees', default=10)

#     parser.add_argument('--L', type=int, choices=range(1, 15000, 1),
#                         help='The size of the candidate window', default=1000)
#     args = parser.parse_args()
    
    args = argparse.Namespace(S=4, L=300) #TODO remove this when not using jupyter notebook, its needed so arguments dont brick the code
    main(args.S, args.L)


Number of learners: 4
Candidate window size: 300
SWAPPED ( 0.0  >  0.0 )
Ensemble: 0.00 Candidate: 0.00 Trees: [Accuracy: 0.00%, Accuracy: 0.00%, Accuracy: 0.00%, Accuracy: 0.00%]
Ensemble: 0.50 Candidate: 0.00 Trees: [Accuracy: 50.00%, Accuracy: 50.00%, Accuracy: 50.00%, Accuracy: 50.00%]
Ensemble: 0.33 Candidate: 0.00 Trees: [Accuracy: 33.33%, Accuracy: 33.33%, Accuracy: 33.33%, Accuracy: 33.33%]
Ensemble: 0.50 Candidate: 0.00 Trees: [Accuracy: 50.00%, Accuracy: 50.00%, Accuracy: 50.00%, Accuracy: 50.00%]
Ensemble: 0.40 Candidate: 0.00 Trees: [Accuracy: 40.00%, Accuracy: 40.00%, Accuracy: 40.00%, Accuracy: 40.00%]
Ensemble: 0.33 Candidate: 0.17 Trees: [Accuracy: 33.33%, Accuracy: 33.33%, Accuracy: 33.33%, Accuracy: 33.33%]
Ensemble: 0.29 Candidate: 0.14 Trees: [Accuracy: 28.57%, Accuracy: 28.57%, Accuracy: 28.57%, Accuracy: 28.57%]
Ensemble: 0.38 Candidate: 0.12 Trees: [Accuracy: 37.50%, Accuracy: 37.50%, Accuracy: 37.50%, Accuracy: 37.50%]
Ensemble: 0.44 Candidate: 0.22 Trees: [Accu

Ensemble: 0.81 Candidate: 0.80 Trees: [Accuracy: 80.09%, Accuracy: 82.74%, Accuracy: 79.65%, Accuracy: 79.20%]
Ensemble: 0.81 Candidate: 0.80 Trees: [Accuracy: 80.18%, Accuracy: 82.82%, Accuracy: 79.74%, Accuracy: 78.85%]
Ensemble: 0.81 Candidate: 0.80 Trees: [Accuracy: 80.26%, Accuracy: 82.89%, Accuracy: 79.82%, Accuracy: 78.95%]
Ensemble: 0.81 Candidate: 0.80 Trees: [Accuracy: 80.35%, Accuracy: 82.97%, Accuracy: 79.91%, Accuracy: 79.04%]
Ensemble: 0.80 Candidate: 0.80 Trees: [Accuracy: 80.00%, Accuracy: 82.61%, Accuracy: 80.00%, Accuracy: 78.70%]
Ensemble: 0.81 Candidate: 0.80 Trees: [Accuracy: 80.09%, Accuracy: 82.68%, Accuracy: 80.09%, Accuracy: 78.79%]
Ensemble: 0.81 Candidate: 0.80 Trees: [Accuracy: 79.74%, Accuracy: 82.76%, Accuracy: 80.17%, Accuracy: 78.45%]
Ensemble: 0.81 Candidate: 0.80 Trees: [Accuracy: 79.83%, Accuracy: 82.83%, Accuracy: 79.83%, Accuracy: 78.11%]
Ensemble: 0.81 Candidate: 0.80 Trees: [Accuracy: 79.91%, Accuracy: 82.91%, Accuracy: 79.91%, Accuracy: 78.21%]
E

Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.19%, Accuracy: 84.21%, Accuracy: 80.36%, Accuracy: 82.79%]
Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.22%, Accuracy: 84.04%, Accuracy: 80.40%, Accuracy: 82.83%]
Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.26%, Accuracy: 84.07%, Accuracy: 80.44%, Accuracy: 82.86%]
Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.29%, Accuracy: 84.10%, Accuracy: 80.48%, Accuracy: 82.90%]
Ensemble: 0.84 Candidate: 0.81 Trees: [Accuracy: 82.33%, Accuracy: 84.14%, Accuracy: 80.52%, Accuracy: 82.93%]
Ensemble: 0.84 Candidate: 0.81 Trees: [Accuracy: 82.36%, Accuracy: 84.17%, Accuracy: 80.56%, Accuracy: 82.97%]
Ensemble: 0.84 Candidate: 0.81 Trees: [Accuracy: 82.40%, Accuracy: 84.20%, Accuracy: 80.60%, Accuracy: 83.00%]
Ensemble: 0.84 Candidate: 0.81 Trees: [Accuracy: 82.44%, Accuracy: 84.23%, Accuracy: 80.64%, Accuracy: 83.03%]
Ensemble: 0.84 Candidate: 0.81 Trees: [Accuracy: 82.47%, Accuracy: 84.26%, Accuracy: 80.68%, Accuracy: 83.07%]
E

Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.64%, Accuracy: 83.29%, Accuracy: 79.15%, Accuracy: 82.90%]
Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.66%, Accuracy: 83.31%, Accuracy: 79.17%, Accuracy: 82.92%]
Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.69%, Accuracy: 83.33%, Accuracy: 79.20%, Accuracy: 82.95%]
Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.58%, Accuracy: 83.23%, Accuracy: 79.10%, Accuracy: 82.84%]
Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.60%, Accuracy: 83.25%, Accuracy: 79.12%, Accuracy: 82.86%]
Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.63%, Accuracy: 83.27%, Accuracy: 79.15%, Accuracy: 82.88%]
Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.65%, Accuracy: 83.29%, Accuracy: 79.18%, Accuracy: 82.90%]
Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.67%, Accuracy: 83.31%, Accuracy: 79.20%, Accuracy: 82.93%]
Ensemble: 0.84 Candidate: 0.80 Trees: [Accuracy: 82.69%, Accuracy: 83.21%, Accuracy: 79.23%, Accuracy: 82.82%]
E

Ensemble: 0.82 Candidate: 0.79 Trees: [Accuracy: 80.63%, Accuracy: 82.39%, Accuracy: 78.38%, Accuracy: 81.02%]
Ensemble: 0.82 Candidate: 0.79 Trees: [Accuracy: 80.65%, Accuracy: 82.40%, Accuracy: 78.40%, Accuracy: 81.04%]
Ensemble: 0.82 Candidate: 0.79 Trees: [Accuracy: 80.66%, Accuracy: 82.42%, Accuracy: 78.42%, Accuracy: 81.05%]
Ensemble: 0.82 Candidate: 0.79 Trees: [Accuracy: 80.68%, Accuracy: 82.44%, Accuracy: 78.44%, Accuracy: 80.98%]
Ensemble: 0.82 Candidate: 0.79 Trees: [Accuracy: 80.70%, Accuracy: 82.46%, Accuracy: 78.46%, Accuracy: 80.99%]
Ensemble: 0.82 Candidate: 0.79 Trees: [Accuracy: 80.72%, Accuracy: 82.38%, Accuracy: 78.38%, Accuracy: 80.92%]
Ensemble: 0.82 Candidate: 0.79 Trees: [Accuracy: 80.74%, Accuracy: 82.30%, Accuracy: 78.31%, Accuracy: 80.84%]
Ensemble: 0.82 Candidate: 0.79 Trees: [Accuracy: 80.76%, Accuracy: 82.31%, Accuracy: 78.33%, Accuracy: 80.86%]
Ensemble: 0.82 Candidate: 0.79 Trees: [Accuracy: 80.68%, Accuracy: 82.33%, Accuracy: 78.35%, Accuracy: 80.87%]
E

...

Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.82%, Accuracy: 71.69%, Accuracy: 71.22%, Accuracy: 71.50%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.81%, Accuracy: 71.69%, Accuracy: 71.22%, Accuracy: 71.49%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.81%, Accuracy: 71.69%, Accuracy: 71.22%, Accuracy: 71.49%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.81%, Accuracy: 71.69%, Accuracy: 71.22%, Accuracy: 71.49%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.81%, Accuracy: 71.69%, Accuracy: 71.22%, Accuracy: 71.49%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.81%, Accuracy: 71.69%, Accuracy: 71.22%, Accuracy: 71.49%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.81%, Accuracy: 71.69%, Accuracy: 71.22%, Accuracy: 71.49%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.81%, Accuracy: 71.69%, Accuracy: 71.22%, Accuracy: 71.50%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.81%, Accuracy: 71.69%, Accuracy: 71.22%, Accuracy: 71.49%]
E

Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.84%, Accuracy: 71.73%, Accuracy: 71.17%, Accuracy: 71.52%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.84%, Accuracy: 71.73%, Accuracy: 71.17%, Accuracy: 71.52%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.84%, Accuracy: 71.73%, Accuracy: 71.16%, Accuracy: 71.52%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.84%, Accuracy: 71.73%, Accuracy: 71.17%, Accuracy: 71.52%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.84%, Accuracy: 71.73%, Accuracy: 71.17%, Accuracy: 71.52%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.84%, Accuracy: 71.73%, Accuracy: 71.16%, Accuracy: 71.52%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.84%, Accuracy: 71.73%, Accuracy: 71.17%, Accuracy: 71.52%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.83%, Accuracy: 71.73%, Accuracy: 71.16%, Accuracy: 71.52%]
Ensemble: 0.76 Candidate: 0.66 Trees: [Accuracy: 70.84%, Accuracy: 71.73%, Accuracy: 71.16%, Accuracy: 71.52%]
E

Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.65%, Accuracy: 71.58%, Accuracy: 71.08%, Accuracy: 71.39%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.65%, Accuracy: 71.58%, Accuracy: 71.09%, Accuracy: 71.39%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.65%, Accuracy: 71.58%, Accuracy: 71.09%, Accuracy: 71.39%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.65%, Accuracy: 71.58%, Accuracy: 71.09%, Accuracy: 71.39%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.65%, Accuracy: 71.58%, Accuracy: 71.08%, Accuracy: 71.38%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.65%, Accuracy: 71.58%, Accuracy: 71.08%, Accuracy: 71.38%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.65%, Accuracy: 71.58%, Accuracy: 71.08%, Accuracy: 71.39%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.65%, Accuracy: 71.58%, Accuracy: 71.08%, Accuracy: 71.39%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.65%, Accuracy: 71.58%, Accuracy: 71.08%, Accuracy: 71.39%]
E

Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.56%, Accuracy: 71.56%, Accuracy: 71.05%, Accuracy: 71.30%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.56%, Accuracy: 71.56%, Accuracy: 71.05%, Accuracy: 71.30%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.56%, Accuracy: 71.56%, Accuracy: 71.05%, Accuracy: 71.30%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.56%, Accuracy: 71.56%, Accuracy: 71.05%, Accuracy: 71.30%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.57%, Accuracy: 71.56%, Accuracy: 71.05%, Accuracy: 71.31%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.56%, Accuracy: 71.56%, Accuracy: 71.05%, Accuracy: 71.30%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.56%, Accuracy: 71.56%, Accuracy: 71.05%, Accuracy: 71.30%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.56%, Accuracy: 71.56%, Accuracy: 71.05%, Accuracy: 71.30%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.56%, Accuracy: 71.56%, Accuracy: 71.05%, Accuracy: 71.30%]
E

Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.44%, Accuracy: 71.53%, Accuracy: 70.95%, Accuracy: 71.18%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.44%, Accuracy: 71.53%, Accuracy: 70.95%, Accuracy: 71.18%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.43%, Accuracy: 71.53%, Accuracy: 70.95%, Accuracy: 71.17%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.44%, Accuracy: 71.53%, Accuracy: 70.95%, Accuracy: 71.18%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.43%, Accuracy: 71.53%, Accuracy: 70.95%, Accuracy: 71.17%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.43%, Accuracy: 71.53%, Accuracy: 70.95%, Accuracy: 71.17%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.43%, Accuracy: 71.53%, Accuracy: 70.95%, Accuracy: 71.18%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.43%, Accuracy: 71.53%, Accuracy: 70.95%, Accuracy: 71.18%]
Ensemble: 0.75 Candidate: 0.66 Trees: [Accuracy: 70.43%, Accuracy: 71.53%, Accuracy: 70.95%, Accuracy: 71.18%]
E